In [1]:
import pandas as pd
import re
import requests
from bs4 import BeautifulSoup
import unicodedata

from selenium import webdriver
from selenium.webdriver.common.keys import Keys

#from tqdm import tqdm_notebook as tqdm

from pw import username
from pw import password

In [3]:
def scrape(url):
    page = requests.get(url)
    soup = BeautifulSoup(page.text, 'html.parser')
    return soup

In [4]:
url = "https://www.whiskybase.com/account/login?return=https%3A%2F%2Fwww.whiskybase.com%2Fwhiskies%2Ftop1000"
driver = webdriver.Chrome('/Users/chrisriggio/Downloads/chromedriver')
driver.get(url)

# Using selenium to log into the site with provided username/password
element = driver.find_element_by_name("username")
element.click()
element.send_keys(username)
element = driver.find_element_by_name("password")
element.click()
element.send_keys(password)
element.send_keys(Keys.ENTER)



url = 'https://www.whiskybase.com/whiskies/new-releases'
driver.get(url)
soup = BeautifulSoup(driver.page_source, 'html.parser')

In [5]:
soup

<html class="js" lang="en"><head>
<meta charset="utf-8"/>
<meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<script async="" src="https://www.google-analytics.com/analytics.js"></script><script>document.documentElement.className += 'js'</script>
<link href="https://assets.whiskybase.com/assets/css/wb.css?20191129" rel="stylesheet" type="text/css"/>
<link href="https://assets.whiskybase.com/assets/css/themes/base.css?20191129" rel="stylesheet" type="text/css"/>
<link href="https://assets.whiskybase.com/assets/css/imagezoom.css?20191129" rel="stylesheet" type="text/css"/>
<link href="https://www.whiskybase.com/whiskies/new-releases" rel="canonical"/>
<title>New releases - Whiskybase - Ratings and reviews for whisky</title>
<meta content="#7f7a4a" name="theme-color"/>
<meta content="#7f7a4a" name="msapplication-navbutton-color"/>
<meta content="#7f7a4a" name="apple-mobile-web-app-status-bar-style"/>
<meta content="Whiskybase: discover new bottles, track your collecti

In [6]:
cols = soup.find_all('tr')

In [7]:
col_comp = [cols[0].find_all('th')[col].text[14:-12] for col in range(1,8)]
col_comp

['Name', 'Stated Age', 'Strength', 'Size', 'Bottled', 'Casknumber', 'Rating']

In [8]:
#names
soup.find_all('a', {'class': 'clickable'})[0].text

'10th Street Peated Single Malt '

In [9]:
#td class="data text-right">
test1 = soup.find_all('td')
test1[7].text#[1:-2]

'94.00'

In [10]:
#a class="sort"
soup.find_all('td')[0]

<td class="photo buttons">
<a class="photo photo-popup" data-photo="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-big.jpg" href="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-big.jpg"><img alt="10th Street Peated Single Malt" class="bottle-preview small unveil" data-src="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-small.png" onerror="this.parentElement.style.display='none';this.parentElement.classList.remove('photo-popup');" src="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-small.png"/></a>
</td>

In [11]:
#a class="photo photo-popup"
soup.find_all('a', {'class': 'photo photo-popup'})[0]

<a class="photo photo-popup" data-photo="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-big.jpg" href="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-big.jpg"><img alt="10th Street Peated Single Malt" class="bottle-preview small unveil" data-src="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-small.png" onerror="this.parentElement.style.display='none';this.parentElement.classList.remove('photo-popup');" src="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-small.png"/></a>

In [12]:
#a class="clickable" 
soup.find_all('a', {'class': 'clickable'})[0].text

'10th Street Peated Single Malt '

In [13]:
whisky_num = len(soup.find_all('a', {'class': 'clickable'}))
whisky_num

5577

In [38]:
namelist = []

for i in range(0, whisky_num):
    name = soup.find_all('a', {'class': 'clickable'})[i].text
    namelist.append(name)

In [37]:
numb = len(soup.find_all('td', {'class': 'data text-right'}))
numb

44616

In [35]:
stated_age = []
for i in range(0, numb, 8):
    age = soup.find_all('td', {'class': 'data text-right'})[i].text
    if age == '':
        stated_age.append(None)
    else:
        stated_age.append(age)

In [34]:
strength = []
for i in range(1, numb, 8):
    vol = soup.find_all('td', {'class': 'data text-right'})[i].text
    if vol == '':
        strength.append(None)
    else:
        strength.append(vol)

In [33]:
size = []

for i in range(2, numb, 8):
    s = soup.find_all('td', {'class': 'data text-right'})[i].text
    if s == '':
        size.append(None)
    else:
        size.append(s)

In [24]:
rating = []

for r in range(5, numb, 8):
    rate = soup.find_all('td', {'class': 'data text-right'})[r].text
    if rate == '':
        rating.append(None)
    else:
        rating.append(rate)

In [25]:
print(len(rating))
print(len(size))
print(len(strength))
print(len(stated_age))
print(len(namelist))

5577
5577
5577
5577
5577


In [26]:
df = pd.DataFrame(namelist, columns = ['Name'])

df['Stated Age'] = stated_age
df['Strength'] = strength
df['Size'] = size
df['Rating'] = rating

In [30]:
df.head(10)

Name Stated Age     Strength  \
0                    10th Street Peated Single Malt        None  46.0 % Vol.   
1                       10th Street STR Single Malt        None  46.0 % Vol.   
2             1770 Glasgow Single Malt  2019 Release       None  46.0 % Vol.   
3   1770 Glasgow Single Malt - Peated  Release No. 1       None  46.0 % Vol.   
4              1792 Full Proof  Single Barrel Select       None  62.5 % Vol.   
5  A Distillery in Orkney 2011 MMcK  Càrn Mòr - S...       None  54.8 % Vol.   
6  A Dream of Scotland 16-year-old BW  Happy Hall...         16  56.5 % Vol.   
7           A Dream of Scotland 2002 BW  Autumn Lady         17  50.2 % Vol.   
8  A Dream of Scotland 2005 BW  Unknown South Isl...         14  55.2 % Vol.   
9         A Dream of Scotland 2006 BW  Unknown Islay         13  57.3 % Vol.   

     Size Rating  
0  750 ml  94.00  
1  750 ml   None  
2  500 ml  82.97  
3  500 ml  83.75  
4  750 ml   None  
5  700 ml   None  
6  500 ml  87.25  
7  700 ml  88.67  
8  700 ml   None  
9  700 ml  86.45

In [31]:
df.to_csv('bottles_2019.csv')